# NYC Taxi Trip Duration Regression 
This notebook shows how to train a model for NYC taxi trip duration regression with MLFlow, Databricks AutoML and various methods. 

This showcases: 
- 1. AutoML
- 1. XGBoost model + Hyperparameter Tuning with Grid Search / Random Search
- 2. Logging MLFlow experiments
- 3. Model Versioning in MLFlow Registry
- 4. Deployment to Online Serving Endpoint
- 5. Deployment with Traffic Splitting
- 6. Model Monitoring [TODO] 
- 7. GitLab Integration and CI/CD
- 10. A/B Testing [TODO] 

## Preparing the data and environment

### Load Data Tables 

In [0]:
target_column = "trip_duration"
df_train = spark.read.table("jn_catalog.datasets.nyc_taxi")
df_test = spark.read.table("jn_catalog.datasets.nyc_taxi")

In [0]:
from pyspark.sql.functions import col
from pyspark.sql.types import IntegerType, FloatType, TimestampType

# Convert table format types
def convert_nyc_dataset_types(df):
    df = df.withColumn("pickup_datetime", col("pickup_datetime").cast(TimestampType()))
    df = df.withColumn("dropoff_datetime", col("dropoff_datetime").cast(TimestampType()))
    df = df.withColumn("vendor_id", col("vendor_id").cast(IntegerType()))
    df = df.withColumn("passenger_count", col("passenger_count").cast(IntegerType()))
    df = df.withColumn("trip_duration", col("trip_duration").cast(IntegerType()))
    df = df.withColumn("pickup_longitude", col("pickup_longitude").cast(FloatType()))
    df = df.withColumn("pickup_latitude", col("pickup_latitude").cast(FloatType()))
    df = df.withColumn("dropoff_longitude", col("dropoff_longitude").cast(FloatType()))
    df = df.withColumn("dropoff_latitude", col("dropoff_latitude").cast(FloatType()))
    return df

# Display the updated schema
df_train = convert_nyc_dataset_types(df_train)
df_test = convert_nyc_dataset_types(df_test)

In [0]:
# Remove outliers
df_train = df_train.filter(df_train.trip_duration < 5000)

In [0]:
# Use numerical columns
supported_cols = ["pickup_latitude", "passenger_count", "dropoff_latitude",  "store_and_fwd_flag", "pickup_longitude", "vendor_id", "dropoff_longitude"] 

In [0]:
display(df_train)

id vendor_id pickup_datetime dropoff_datetime passenger_count pickup_longitude pickup_latitude dropoff_longitude dropoff_latitude store_and_fwd_flag trip_duration id1589506 2 2016-04-02T17:41:37Z 2016-04-02T17:57:33Z 5 -73.98481 40.7794 -73.95901 40.81976 N 956 id1081378 1 2016-05-17T03:41:22Z 2016-05-17T03:52:33Z 1 -74.00285 40.724976 -73.98433 40.69166 N 671 id2988321 2 2016-04-01T08:19:39Z 2016-04-01T08:27:36Z 1 -73.97863 40.74494 -73.98856 40.73726 N 477 id2759902 1 2016-06-27T06:00:56Z 2016-06-27T06:43:14Z 1 -73.8787 40.73727 -73.938126 40.82818 N 2538 id0965960 1 2016-03-22T08:02:22Z 2016-03-22T08:48:16Z 1 -73.87108 40.773678 -73.98293 40.73507 N 2754 id2572605 2 2016-01-12T23:59:57Z 2016-01-13T00:08:19Z 1 -74.00679 40.74063 -73.9847 40.76846 N 502 id1318259 2 2016-02-13T21:36:39Z 2016-02-13T21:50:20Z 1 -73.99723 40.72539 -73.98434 40.71702 N 821 id0687270 1 2016-01-08T12:24:26Z 2016-01-08T12:54:03Z 1 -73.97822 40.766586 -73.9274 40.762825 N 1777 id1749451 2 2016-06-14T08:02:56Z 2016-06-14T08:17:43Z 6 -73.98128 40.74741 -73.98405 40.75929 N 887 id2940014 2 2016-01-01T13:21:35Z 2016-01-01T13:39:17Z 1 -73.94763 40.77515 -73.99707 40.73395 N 1062 id1127600 2 2016-03-12T21:40:12Z 2016-03-12T21:51:55Z 3 -73.979515 40.743736 -73.95803 40.76172 N 703 id0160200 1 2016-03-31T06:25:09Z 2016-03-31T06:34:48Z 1 -73.998245 40.760822 -73.97383 40.750328 N 579 id2902017 1 2016-05-21T16:18:07Z 2016-05-21T16:57:48Z 1 -73.97349 40.763554 -74.014946 40.71139 N 2381 id0639236 1 2016-05-11T21:00:31Z 2016-05-11T21:16:12Z 1 -73.989395 40.74143 -73.97344 40.755657 N 941 id3752165 2 2016-02-19T14:33:50Z 2016-02-19T14:57:19Z 1 -73.96979 40.763275 -73.97623 40.724564 N 1409 id3491988 1 2016-05-22T01:16:21Z 2016-05-22T01:25:35Z 1 -73.95597 40.776093 -73.96756 40.800266 N 554 id2820679 2 2016-06-15T09:12:11Z 2016-06-15T10:08:27Z 1 -73.8577 40.70538 -73.9868 40.74617 N 3376 id3264247 1 2016-01-10T21:21:12Z 2016-01-10T21:41:37Z 2 -73.99322 40.736485 -73.95025 40.787327 N 1225 id3478915 1 2016-02-20T00:17:05Z 2016-02-20T00:41:13Z 1 -73.978325 40.752213 -74.01131 40.71402 N 1448 id3475671 2 2016-05-02T13:52:58Z 2016-05-02T14:05:45Z 2 -73.99144 40.75024 -73.98918 40.72691 N 767 id3275209 2 2016-05-26T09:03:15Z 2016-05-26T09:06:43Z 5 -73.965935 40.76849 -73.96928 40.763813 N 208 id1070101 2 2016-05-15T10:31:34Z 2016-05-15T10:51:34Z 1 -73.946976 40.776104 -73.82224 40.726532 N 1200 id1722005 1 2016-05-20T23:55:26Z 2016-05-20T23:57:31Z 2 -73.98929 40.7425 -73.99469 40.735752 N 125 id0550983 1 2016-04-05T22:34:27Z 2016-04-05T22:40:20Z 1 -73.98549 40.738567 -73.98344 40.726315 N 353 id2993520 2 2016-06-10T06:46:15Z 2016-06-10T07:04:40Z 1 -73.95999 40.77118 -73.87086 40.77383 N 1105 id1195357 2 2016-02-23T06:32:45Z 2016-02-23T06:45:22Z 1 -73.95761 40.76598 -73.98939 40.7465 N 757 id2956823 2 2016-03-24T10:52:36Z 2016-03-24T11:14:23Z 1 -73.98187 40.776398 -73.940735 40.811756 N 1307 id2176400 1 2016-02-09T15:21:41Z 2016-02-09T15:31:59Z 1 -73.98553 40.741684 -73.97987 40.752636 N 618 id3731617 1 2016-04-19T11:18:04Z 2016-04-19T11:32:09Z 1 -73.95512 40.765194 -73.937515 40.753944 N 845 id0678699 2 2016-06-21T21:09:07Z 2016-06-21T21:25:57Z 3 -73.98562 40.723175 -73.99717 40.74685 N 1010 id1372408 2 2016-01-31T01:40:27Z 2016-01-31T01:45:41Z 1 -73.99348 40.74155 -73.99175 40.74669 N 314 id0894794 2 2016-06-08T17:11:49Z 2016-06-08T18:00:06Z 3 -73.90692 40.87682 -73.94146 40.79863 N 2897 id3205277 2 2016-04-13T21:13:20Z 2016-04-13T21:21:11Z 3 -74.00896 40.71617 -74.00636 40.72187 N 471 id0521210 2 2016-02-08T16:53:18Z 2016-02-08T17:03:33Z 1 -73.99809 40.735657 -73.980286 40.754868 N 615 id2845653 2 2016-06-28T13:01:50Z 2016-06-28T13:13:57Z 1 -73.97572 40.75252 -73.99115 40.74301 N 727 id3017709 2 2016-03-23T01:32:04Z 2016-03-23T01:41:54Z 1 -73.99994 40.730297 -73.98196 40.765945 N 590 id3588054 2 2016-02-13T19:51:20Z 2016-02-13T20:00:03Z 1 -73.98044 40.73031 -74.00218 40.73288 N 523 id0392541 2 2016-02-19T13:13:55Z 2016-02-19T13:27:36Z 1 -73.97279 40.764893 -73.98556 4

## 1-2. Model Training

Covers (1) and (2):
- AutoML
- Custom XGBoost
- Grid Search
- Random Search
- Experiment Logging 
- Metric Logging


### With AutoML 

In [0]:
import databricks.automl as db_automl
summary_rg = db_automl.regress(df_train, target_col=target_column, primary_metric="rmse", timeout_minutes=10)

In [0]:
import mlflow 
from mlflow.models.signature import infer_signature

# Creating sample input to be logged
df_sample = df_train.limit(10).toPandas()
x_sample = df_sample.drop(columns=[target_column])
y_sample = df_sample[target_column]

# Getting the model created by AutoML 
best_model = summary_rg.best_trial.load_model()

env = mlflow.pyfunc.get_default_conda_env()
with open(mlflow.artifacts.download_artifacts("runs:/"+summary_rg.best_trial.mlflow_run_id+"/model/requirements.txt"), 'r') as f:
    env['dependencies'][-1]['pip'] = f.read().split('\n')

# Create a new run in the same experiment as our automl run.
with mlflow.start_run(run_name="taxi_duration_run", experiment_id=summary_rg.experiment.experiment_id) as run:
  mlflow.sklearn.log_model(
              sk_model=best_model, # object of your model
              artifact_path="model", #name of the artifact under MLFlow
              input_example=x_sample, # example of the dataset, should be Pandas
              signature=infer_signature(x_sample, y_sample), # schema of the dataset, not necessary with FS, but nice to have 
              conda_env = env
          )
  mlflow.log_metrics(summary_rg.best_trial.metrics)
  mlflow.log_params(summary_rg.best_trial.params)


### With Random Search - XGBoost

In [0]:
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import GradientBoostingRegressor

import pyspark.pandas as ps
import pandas as pd
import mlflow 
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error

supported_cols = ["pickup_latitude", "passenger_count", "dropoff_latitude", "pickup_longitude", "vendor_id", "dropoff_longitude"]

train_X = df_train.toPandas()[supported_cols]
train_y = df_train.toPandas()[target_column]
test_X = df_test.toPandas()[supported_cols]
test_y = df_test.toPandas()[target_column]

xgb = GradientBoostingRegressor(random_state=9)
param_grid = {
    'n_estimators': [10, 20],
    'max_leaf_nodes': [25, 50],
    'max_depth': [5]
}

# Use gradient boosting regressor while defining the estimator for grid search 
search = RandomizedSearchCV(xgb, param_grid, cv=2, n_iter=2, refit=True)
search.fit(train_X, train_y)

### With Grid Search - XGBoost

In [0]:
import pyspark.pandas as ps
import pandas as pd
import mlflow
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error

supported_cols = ["pickup_latitude", "passenger_count", "dropoff_latitude", "pickup_longitude", "vendor_id", "dropoff_longitude"]

train_X = df_train.toPandas()[supported_cols]
train_y = df_train.toPandas()[target_column]
test_X = df_test.toPandas()[supported_cols]
test_y = df_test.toPandas()[target_column]

xgb = GradientBoostingRegressor(random_state=9)
param_grid = {
    'n_estimators': [10, 20],
    #'max_leaf_nodes': [25, 50],
    'max_depth': [5]
}

# Use gradient boosting regressor while defining the estimator for grid search 
grid = GridSearchCV(xgb, param_grid, cv=2, refit=True)
grid.fit(train_X, train_y)

## 3. Model Saving and Versioning

In [0]:
model_name = "taxi_duration_model"
model_registered = mlflow.register_model(f"runs:/{run.info.run_id}/model", model_name)

# Transition the Model to Production
client = mlflow.tracking.MlflowClient()
print("registering model version " + model_registered.version + " as production model")
client.transition_model_version_stage(model_name, model_registered.version, stage = "Production", archive_existing_versions=True)

## 4. Model Deployment to Serving Endpoint

In [0]:
import requests
import json

# Model variables from the model registry
endpoint_name = "taxi-duration-endpoint"
model_version = model_registered.version

# Get API token info from notebook context
ctx = dbutils.notebook.entry_point.getDbutils().notebook().getContext()
token = ctx.apiToken().getOrElse(None)
url = ctx.apiUrl().getOrElse(None)

# Define the API endpoint URL
#endpoint_url = f"{url}/api/2.0/serving-endpoints"
endpoint_url = f"{url}/api/2.0/preview/serving-endpoints" # Inference table

# Define the request payload
payload = {
    "name": endpoint_name,
    "config": {
        "served_models": [{
            "name": model_name,             # Deployment name
            "model_name": model_name,       # Model to deploy from MLFlow registry
            "model_version": model_version,
            "workload_size": "Small",
            "scale_to_zero_enabled": True
        }]

    # # Uncomment when inference table is enabled
    },
    "inference_table_config": {
        "dbfs_destination_path": "dbfs:/Users/julie.nguyen@databricks.com/inference_table"

    }
}

# Set the headers and authentication token
headers = {
    "Authorization": f"Bearer {token}",
    "Content-Type": "application/json"
}


# Make the API request
response = requests.post(endpoint_url, headers=headers, data=json.dumps(payload))

# Check the status code of the response
if response.status_code == 200:
    print("Endpoint created successfully")
else:
    print("Error creating endpoint:", response.content)

if ("inference_table_config" in response.json()):
    print("Inference Tables was successfully enabled with inference_table_config:", response.json()["inference_table_config"])
else:
    print("Warning: Inference Tables was not enabled. Please ensure the feature is enabled on your workspace.")


In [0]:
model_registered.version

## 5. Traffic Split Deployment

In [0]:
import requests
import json

# Model variables from the model registry
endpoint_name = "taxi-duration-monitored"
model_version = model_registered.version

# Get API token info from notebook context
ctx = dbutils.notebook.entry_point.getDbutils().notebook().getContext()
token = ctx.apiToken().getOrElse(None)
url = ctx.apiUrl().getOrElse(None)

# Define the API endpoint URL
endpoint_url = f"{url}/api/2.0/serving-endpoints/{endpoint_name}/config"

# Define the request payload
payload = {
        "served_models": [{
            "name": model_name,
            "model_name": model_name,
            "model_version": model_version - 1,
            "workload_size": "Small",
            "scale_to_zero_enabled": True
        },              
        {
            "name": model_name + "_new",
            "model_name": model_name,
            "model_version": model_version,
            "workload_size": "Small",
            "scale_to_zero_enabled": True
            }]
    ,
        
    "traffic_config": {
      "routes": [
        {
          "served_model_name": "taxi_duration_model-10",
          "traffic_percentage": 50
        },
        {
        "served_model_name": "taxi_duration_model-new",
          "traffic_percentage": 50
        }
      ]
    }
}

# Set the headers and authentication token
headers = {
    "Authorization": f"Bearer {token}",
    "Content-Type": "application/json"
}

# Make the API request
response = requests.put(endpoint_url, headers=headers, data=json.dumps(payload))

# Check the status code of the response
if response.status_code == 200:
    print("Endpoint updated successfully")
else:
    print("Error updating endpoint:", response.content)

## 6. Model Monitoring

## 10. A/B Testing

In [0]:
df = spark.read.format("delta").load("dbfs:/Users/julie.nguyen@databricks.com/inference_table/taxi-duration-monitored")


In [0]:
display(df)

In [0]:
# generate truth_label


# compute metric for each